In [0]:
from pyspark.sql.functions import *
from pyspark.sql.types import *
from pyspark.sql import functions as F

In [0]:
dbutils.fs.mount(
    source="wasbs://paris-olympic-data@parisolympicadls.blob.core.windows.net",
    mount_point="/mnt/paris-olympic-data",
    extra_configs={"fs.azure.account.key.parisolympicadls.blob.core.windows.net":"lHTB8xfM/KqJ6dvFCOjlHy+3TFDQHtySPfVR8lyjsa5h9qD5Bjw4BMSdfCdOnHppGh8j8TKiBGTk+ASt8WI8Yg=="}
)

---------------------------------------------------------------------------
ExecutionError                            Traceback (most recent call last)
File <command-2870689215623716>, line 1
----> 1 dbutils.fs.mount(
      2     source="wasbs://paris-olympic-data@parisolympicadls.blob.core.windows.net",
      3     mount_point="/mnt/paris-olympic-data",
      4     extra_configs={"fs.azure.account.key.parisolympicadls.blob.core.windows.net":"lHTB8xfM/KqJ6dvFCOjlHy+3TFDQHtySPfVR8lyjsa5h9qD5Bjw4BMSdfCdOnHppGh8j8TKiBGTk+ASt8WI8Yg=="}
      5 )

File /databricks/python_shell/dbruntime/dbutils.py:158, in prettify_exception_message.<locals>.f_with_exception_handling(*args, **kwargs)
    156 exc.__context__ = None
    157 exc.__cause__ = None
--> 158 raise exc

ExecutionError: An error occurred while calling o417.mount.
: java.rmi.RemoteException: java.lang.IllegalArgumentException: requirement failed: Directory already mounted: /mnt/paris-olympic-data; nested exception is: 
	java.lang.Illeg

In [0]:
dbutils.fs.ls("/mnt/paris-olympic-data")

[FileInfo(path='dbfs:/mnt/paris-olympic-data/raw-data/', name='raw-data/', size=0, modificationTime=0),
 FileInfo(path='dbfs:/mnt/paris-olympic-data/transformed-data/', name='transformed-data/', size=0, modificationTime=0)]

In [0]:
%fs
ls "/mnt/paris-olympic-data"

path name size modificationTime dbfs:/mnt/paris-olympic-data/raw-data/ raw-data/ 0 0 dbfs:/mnt/paris-olympic-data/transformed-data/ transformed-data/ 0 0

In [0]:
coaches=spark.read.format("csv").option("header","true").option("delimiter",",").option("inferSchema","true").load("/mnt/paris-olympic-data/raw-data/coaches.csv")
medals=spark.read.format("csv").option("header","true").option("delimiter",",").option("inferSchema","true").load("/mnt/paris-olympic-data/raw-data/medals.csv")
medallist=spark.read.format("csv").option("header","true").option("delimiter",",").option("inferSchema","true").load("/mnt/paris-olympic-data/raw-data/medallist.csv")
teams=spark.read.format("csv").option("header","true").option("delimiter",",").option("inferSchema","true").load("/mnt/paris-olympic-data/raw-data/teams.csv")


In [0]:
athlete = spark.read.format("csv").option("header", "true").load("/mnt/paris-olympic-data/raw-data/athletes.csv")

In [0]:
#Dropped duplicate values
athlete_df=athlete.dropDuplicates()

In [0]:
#removing rows where all column value is null
athlete_df=athlete_df.na.drop(how='all')

In [0]:
# filling null values with unknown
athlete_df=athlete_df.na.fill(value='Unknown')

In [0]:
#convert birth_date to date type
athlete_df=athlete_df.withColumn("birth_date",F.to_date(col("birth_date"),"yyyy-MM-dd"))

In [0]:
from pyspark.sql.functions import col, regexp_replace
#dropped unnecessary columns
columns_to_drop=['current','name_short','name_tv','function','country_code','country_long','nationality','nationality_long','nationality_code','events','birth_place','residence_place','residence_country','nickname','hobbies','occupation','education','family','lang','reason','hero','influence','philosophy','sporting_relatives','ritual','other_sports','height','weight','coach','birth_country']
athlete_df=athlete_df.drop(*columns_to_drop)
athlete_df=athlete_df.withColumn('disciplines',regexp_replace(col("disciplines"),"[\\[\\]']","")) \
                    .withColumn("disciplines",trim(col("disciplines")))
display(athlete_df)

code name gender country disciplines birth_date 1550150 PAUL Georges Julien Male Mauritius Badminton 1996-01-07 1554968 MEKTIC Nikola Male Croatia Tennis 1988-12-24 1561253 QUINTINO Jessica Female Brazil Handball 1991-04-17 1563335 QUAKE Male Chinese Taipei Breaking 1999-09-21 1564559 TAKAYAWA Gerard Male Fiji Judo 2005-11-07 1566441 FRANK Tanja Female Austria Sailing 1993-01-24 1572558 AASTEDT Sofia Female Sweden Swimming null 1572617 BAUER Christina Female France Volleyball 1988-01-01 1573136 LIZAKOWSKA Weronika Female Poland Athletics 1998-11-02 1879111 OUMIHA Sofiane Male France Boxing 1994-12-23 1879831 FOPPA Pauletta Female France Handball 2000-12-22 1887978 CIOBANU Victor Male Republic of Moldova Wrestling 1992-10-07 1888156 KITAGAWA Hikaru Female Japan Football 1997-05-10 1888973 TOLBA Youssof Male Egypt Archery null 1891002 DAVIDSON Madaline Female New Zealand Trampoline Gymnastics 1999-01-08 1899035 SANFORD Liam Male Great Britain Hockey 1996-03-14 1899257 STOCKSCHLAEDER Johanna Maria Female Germany Handball 1995-02-11 1901562 de la CRUZ de PENA Bethania Female Dominican Republic Volleyball 1987-05-13 1901750 WU Tongtong Female China Basketball 1994-06-27 1901756 SUN Mengran Female China Basketball 1992-07-16 1902180 HASEGAWA Akiko Female Japan Beach Volleyball 1985-11-30 1906480 FINGER Anton Male Germany Rowing 1998-08-01 1907194 SORGIUS Timo Male Germany Swimming null 1907658 DANANI Santiago Male Argentina Volleyball 1995-12-12 1911929 SAIDY Fabrisio Male France Athletics null 1913218 LIN Xiyu Janet Female China Golf 1996-02-25 1917762 SKINNER Avery Female United States Volleyball 1999-04-25 1920302 KRAFZIK Carolina Female Germany Athletics 1995-03-27 1924385 ATKIN Sam Male Great Britain Athletics 1993-03-14 1925355 CHAMIZO MARQUEZ Frank Male Italy Wrestling 1992-07-10 1925641 BERTOCCHI Elena Female Italy Diving null 1925806 BANCHELLI Caterina Female Italy Water Polo 2000-09-25 1539131 BERTEMES Bob Male Luxembourg Athletics 1993-05-24 1539954 WALSH Grainne Female Ireland Boxing 1995-10-13 1551330 NALBANTOVA Kaloyana Female Bulgaria Badminton 2006-03-06 1552154 ACCAME Ilaria Elvira Female Italy Athletics 2001-08-31 1554997 LOEFQVIST Olivia Female Sweden Handball 1998-07-13 1561242 ARENHART Barbara Female Brazil Handball 1986-10-04 1562779 ANDERSON Navasky Male Jamaica Athletics 2000-01-21 1562874 MUELLER Svenja Female Germany Beach Volleyball 2001-02-13 1568167 ONDER Ahmet Male Türkiye Artistic Gymnastics null 1574118 SOYIZWAPI Siviwe Male South Africa Rugby Sevens 1992-12-07 1878450 REINKIND Harald Male Norway Handball 1992-08-17 1878525 BRUN Kristoffer Male Norway Rowing 1988-04-07 1879856 ZAADI DEUNA Grace Female France Handball 1993-07-07 1888831 SEJA Arturas Male Lithuania Canoe Sprint 1996-03-17 1889162 FAROUK Mohamed Male Egypt Diving 2002-12-13 1891289 AGBEGNENOU Clarisse Female France Judo 1992-10-25 1892105 HABARTA Tomas Male Czechia Athletics 2003-07-10 1892647 KWIZERA Rodrigue Male Burundi Athletics null 1895553 BACARI Elie Male Belgium Athletics 2003-10-14 1896822 ALIKULOV Khusniddin Male Uzbekistan Football 1999-04-04 1898472 EMOMALI Nurali Male Tajikistan Judo 2002-04-08 1899731 BECKETT Michael Male Great Britain Sailing 1995-03-27 1901063 FIELDMAN Henry Male Great Britain Rowing 1988-11-25 1901337 NOSKOVA Linda Female Czechia Tennis null 1901954 WATANABE Yuta Male Japan Basketball 1994-10-13 1903122 GOMMERS Aiko Female Belgium Cycling BMX Racing 2004-03-18 1908825 VO Thi Kim Anh Female Vietnam Boxing 1997-07-29 1910646 BONNIN Marie-Julie Female France Athletics 2001-12-17 1912009 RICHARDSON Lewis Male Great Britain Boxing 1997-06-04 1913958 ZHAO Nan Female China Shooting 2004-05-14 1914295 ODKHUU Tsetsentsengel Male Mongolia Judo 1999-10-18 1917792 LIJTENSTEIN Guillermo Male Uruguay Rugby Sevens 1990-09-14 1918706 ISHIKAWA Yuki Male Japan Volleyball 1995-12-11 1921364 RUSSO Roberto Male Italy Volleyball 1997-02-23 1924384 ASHER-SMITH Dina Female Great Britain Athletics null 1924401 CAIRESS Emile Male

In [0]:
#Dropped unnecessary columns
columns_dropped=['code','current','country_code','country','disciplines_code','coaches','coaches_codes','num_coaches','athletes_codes','num_athletes']
teams=teams.drop(*columns_dropped)
# Explode athlete lists into individual records
teams_df=teams.withColumn("athletes",regexp_replace(col("athletes"),"[\\[\\]']","")) \
            .withColumn("athletes",explode(split(col("athletes"),",")))

teams_df=teams_df.withColumn("athletes",trim(col("athletes"))) 

teams_df=teams_df.filter(~(col("Athletes").contains("\\") | col("Athletes").contains('"')))   

display(teams_df)

team team_gender country_long discipline events athletes People's Republic of China M People's Republic of China Archery Men's Team KAO Wenchao People's Republic of China M People's Republic of China Archery Men's Team LI Zhongyuan People's Republic of China M People's Republic of China Archery Men's Team WANG Yan Colombia M Colombia Archery Men's Team ARCILA Santiago Colombia M Colombia Archery Men's Team ENRIQUEZ Jorge Colombia M Colombia Archery Men's Team HERNANDEZ VERA Andres France M France Archery Men's Team ADDIS Baptiste France M France Archery Men's Team CHIRAULT Thomas France M France Archery Men's Team VALLADONT Jean-Charles Great Britain M Great Britain Archery Men's Team HALL Conor Great Britain M Great Britain Archery Men's Team HALL Tom Great Britain M Great Britain Archery Men's Team WISE Alex India M India Archery Men's Team BOMMADEVARA Dhiraj India M India Archery Men's Team JADHAV Pravin Ramesh India M India Archery Men's Team RAI Tarundeep Italy M Italy Archery Men's Team MUSOLESI Federico Italy M Italy Archery Men's Team NESPOLI Mauro Italy M Italy Archery Men's Team PAOLI Alessandro Japan M Japan Archery Men's Team FURUKAWA Takaharu Japan M Japan Archery Men's Team NAKANISHI Junya Japan M Japan Archery Men's Team SAITO Fumiya Kazakhstan M Kazakhstan Archery Men's Team ABDULLIN Ilfat Kazakhstan M Kazakhstan Archery Men's Team YEREMENKO Alexandr Kazakhstan M Kazakhstan Archery Men's Team ZHANGBYRBAY Dauletkeldi Republic of Korea M Republic of Korea Archery Men's Team KIM Je Deok Republic of Korea M Republic of Korea Archery Men's Team KIM Woojin Republic of Korea M Republic of Korea Archery Men's Team LEE Wooseok Mexico M Mexico Archery Men's Team GRANDE Matias Mexico M Mexico Archery Men's Team MARTINEZ WING Bruno Mexico M Mexico Archery Men's Team ROJAS Carlos Chinese Taipei M Chinese Taipei Archery Men's Team LIN Zih-Siang Chinese Taipei M Chinese Taipei Archery Men's Team TANG Chih-Chun Chinese Taipei M Chinese Taipei Archery Men's Team TAI Yu-Hsuan Türkiye M Türkiye Archery Men's Team GAZOZ Mete Türkiye M Türkiye Archery Men's Team TUMER Berkim Türkiye M Türkiye Archery Men's Team YILDIRMIS Abdullah People's Republic of China W People's Republic of China Archery Women's Team AN Qixuan People's Republic of China W People's Republic of China Archery Women's Team LI Jiaman People's Republic of China W People's Republic of China Archery Women's Team YANG Xiaolei France W France Archery Women's Team BARBELIN Lisa France W France Archery Women's Team CORDEAU Amelie France W France Archery Women's Team LOPEZ Caroline Great Britain W Great Britain Archery Women's Team HEALEY Penny Great Britain W Great Britain Archery Women's Team HAVERS Megan Great Britain W Great Britain Archery Women's Team PITMAN Bryony Germany W Germany Archery Women's Team BAUER Katharina Germany W Germany Archery Women's Team KROPPEN Michelle Germany W Germany Archery Women's Team SCHWARZ Charline Indonesia W Indonesia Archery Women's Team CHOIRUNISA Diananda Indonesia W Indonesia Archery Women's Team KAMAL Syifa Nurafifah Indonesia W Indonesia Archery Women's Team OCTAVIA Rezza India W India Archery Women's Team BHAKAT Ankita India W India Archery Women's Team KAUR Bhajan India W India Archery Women's Team KUMARI Deepika Republic of Korea W Republic of Korea Archery Women's Team JEON Hunyoung Republic of Korea W Republic of Korea Archery Women's Team LIM Sihyeon Republic of Korea W Republic of Korea Archery Women's Team NAM Suhyeon Malaysia W Malaysia Archery Women's Team MASHAYIKH Syaqiera Malaysia W Malaysia Archery Women's Team MOHAMAD FAZIL Nurul Azreena Malaysia W Malaysia Archery Women's Team MOHAMAD ZAIRI Ariana Nur Dania Mexico W Mexico Archery Women's Team RUIZ Angela Mexico W Mexico Archery Women's Team VALENCIA Alejandra Mexico W Mexico Archery Women's Team VAZQUEZ Ana Netherlands W Netherlands Archery Women's Team ROEFFEN Quinty Netherlands W Netherlands Archery Women's Team SCHLOESSER Gaby Netherlands W Netherlands Archer

In [0]:
#dropped null columns
ctd=['country_code','country','nationality','nationality_code','team','team_gender','event_type','url_event','code_team']
medallist_df=medallist.drop(*ctd)
display(medallist_df)

medal_date medal_type medal_code name gender country_long nationality_long discipline event birth_date code_athlete is_medallist 2024-07-27 Gold Medal 1.0 EVENEPOEL Remco Male Belgium Belgium Cycling Road Men's Individual Time Trial 2000-01-25 1903136 true 2024-07-27 Silver Medal 2.0 GANNA Filippo Male Italy Italy Cycling Road Men's Individual Time Trial 1996-07-25 1923520 true 2024-07-27 Bronze Medal 3.0 van AERT Wout Male Belgium Belgium Cycling Road Men's Individual Time Trial 1994-09-15 1903147 true 2024-07-27 Gold Medal 1.0 BROWN Grace Female Australia Australia Cycling Road Women's Individual Time Trial 1992-07-07 1940173 true 2024-07-27 Silver Medal 2.0 HENDERSON Anna Female Great Britain Great Britain Cycling Road Women's Individual Time Trial 1998-11-14 1912525 true 2024-07-27 Bronze Medal 3.0 DYGERT Chloe Female United States of America United States of America Cycling Road Women's Individual Time Trial 1997-01-01 1955079 true 2024-07-27 Gold Medal 1.0 OH Sanguk Male Republic of Korea Republic of Korea Fencing Men's Sabre Individual 1996-09-30 1927149 true 2024-07-27 Silver Medal 2.0 FERJANI Fares Male Tunisia Tunisia Fencing Men's Sabre Individual 1997-07-22 1937783 true 2024-07-27 Bronze Medal 3.0 SAMELE Luigi Male Italy Italy Fencing Men's Sabre Individual 1987-07-25 1924595 true 2024-07-27 Gold Medal 1.0 KONG Man Wai Vivian Female Hong Kong, China Hong Kong, China Fencing Women's Épée Individual 1994-02-08 1963262 true 2024-07-27 Silver Medal 2.0 MALLO-BRETON Auriane Female France France Fencing Women's Épée Individual 1993-10-11 1916183 true 2024-07-27 Bronze Medal 3.0 MUHARI Eszter Female Hungary Hungary Fencing Women's Épée Individual 2002-09-30 1946375 true 2024-07-27 Gold Medal 1.0 SMETOV Yeldos Male Kazakhstan Kazakhstan Judo Men -60 kg 1992-09-09 1935408 true 2024-07-27 Silver Medal 2.0 MKHEIDZE Luka Male France France Judo Men -60 kg 1996-01-05 1891304 true 2024-07-27 Bronze Medal 3.0 NAGAYAMA Ryuju Male Japan Japan Judo Men -60 kg 1996-04-15 1896752 true 2024-07-27 Bronze Medal 3.0 GARRIGOS Francisco Male Spain Spain Judo Men -60 kg 1994-12-09 1563544 true 2024-07-27 Gold Medal 1.0 TSUNODA Natsumi Female Japan Japan Judo Women -48 kg 1992-08-06 1896735 true 2024-07-27 Silver Medal 2.0 BAVUUDORJ Baasankhuu Female Mongolia Mongolia Judo Women -48 kg 1999-11-26 1914467 true 2024-07-27 Bronze Medal 3.0 BOUKLI Shirine Female France France Judo Women -48 kg 1999-01-24 1891280 true 2024-07-27 Bronze Medal 3.0 BABULFATH Tara Female Sweden Sweden Judo Women -48 kg 2006-01-03 1571911 true 2024-07-27 Gold Medal 1.0 MAERTENS Lukas Male Germany Germany Swimming Men's 400m Freestyle 2001-12-27 1907192 true 2024-07-27 Silver Medal 2.0 WINNINGTON Elijah Male Australia Australia Swimming Men's 400m Freestyle 2000-05-05 1946172 true 2024-07-27 Bronze Medal 3.0 KIM Woomin Male Republic of Korea Republic of Korea Swimming Men's 400m Freestyle 2001-08-24 4654306 true 2024-07-27 Gold Medal 1.0 TITMUS Ariarne Female Australia Australia Swimming Women's 400m Freestyle 2000-09-07 1946150 true 2024-07-27 Silver Medal 2.0 McINTOSH Summer Female Canada Canada Swimming Women's 400m Freestyle 2006-08-18 1967140 true 2024-07-27 Bronze Medal 3.0 LEDECKY Katie Female United States of America United States of America Swimming Women's 400m Freestyle 1997-03-17 1935938 true 2024-07-28 Gold Medal 1.0 FOX Jessica Female Australia Australia Canoe Slalom Women's Kayak Single 1994-06-11 1940205 true 2024-07-28 Silver Medal 2.0 ZWOLINSKA Klaudia Female Poland Poland Canoe Slalom Women's Kayak Single 1998-12-18 1942126 true 2024-07-28 Bronze Medal 3.0 WOODS Kimberley Female Great Britain Great Britain Canoe Slalom Women's Kayak Single 1995-09-08 1896045 true 2024-07-28 Gold Medal 1.0 FERRAND PREVOT Pauline Female France France Cycling Mountain Bike Women's Cross-country 1992-02-10 1895672 true 2024-07-28 Silver Medal 2.0 BATTEN Haley Female United States of America United States of America Cycling Mountain Bike Women's Cross-country 1998-09-19 19

In [0]:
#writing the data into data lake
athlete_df.repartition(1).write.mode("overwrite").option("header","true").csv("/mnt/paris-olympic-data/transformed-data/athletes")
teams_df.repartition(1).write.mode("overwrite").option("header","true").csv("/mnt/paris-olympic-data/transformed-data/teams")
medals.repartition(1).write.mode("overwrite").option("header","true").csv("/mnt/paris-olympic-data/transformed-data/medals")
medallist_df.repartition(1).write.mode("overwrite").option("header","true").csv("/mnt/paris-olympic-data/transformed-data/medallist")
medals.repartition(1).write.mode("overwrite").option("header","true").csv("/mnt/paris-olympic-data/transformed-data/medals")

In [0]:
#Renaming some columns
medals=(medals.withColumnRenamed("Gold Medal", "Gold_Medal")  
                .withColumnRenamed("Silver Medal", "Silver_Medal")  
                .withColumnRenamed("Bronze Medal", "Bronze_Medal"))

In [0]:
display(medals)

country_code country country_long Gold_Medal Silver_Medal Bronze_Medal Total USA United States United States of America 40 44 42 126 CHN China People's Republic of China 40 27 24 91 JPN Japan Japan 20 12 13 45 AUS Australia Australia 18 19 16 53 FRA France France 16 26 22 64 NED Netherlands Netherlands 15 7 12 34 GBR Great Britain Great Britain 14 22 29 65 KOR Korea Republic of Korea 13 9 10 32 ITA Italy Italy 12 13 15 40 GER Germany Germany 12 13 8 33 NZL New Zealand New Zealand 10 7 3 20 CAN Canada Canada 9 7 11 27 UZB Uzbekistan Uzbekistan 8 2 3 13 HUN Hungary Hungary 6 7 6 19 ESP Spain Spain 5 4 9 18 SWE Sweden Sweden 4 4 3 11 KEN Kenya Kenya 4 2 5 11 NOR Norway Norway 4 1 3 8 IRL Ireland Ireland 4 0 3 7 BRA Brazil Brazil 3 7 10 20 IRI IR Iran Islamic Republic of Iran 3 6 3 12 UKR Ukraine Ukraine 3 5 4 12 ROU Romania Romania 3 4 2 9 GEO Georgia Georgia 3 3 1 7 BEL Belgium Belgium 3 1 6 10 BUL Bulgaria Bulgaria 3 1 3 7 SRB Serbia Serbia 3 1 1 5 CZE Czechia Czechia 3 0 2 5 DEN Denmark Denmark 2 2 5 9 AZE Azerbaijan Azerbaijan 2 2 3 7 CRO Croatia Croatia 2 2 3 7 CUB Cuba Cuba 2 1 6 9 BRN Bahrain Bahrain 2 1 1 4 SLO Slovenia Slovenia 2 1 0 3 TPE Chinese Taipei Chinese Taipei 2 0 5 7 AUT Austria Austria 2 0 3 5 HKG Hong Kong, China Hong Kong, China 2 0 2 4 PHI Philippines Philippines 2 0 2 4 ALG Algeria Algeria 2 0 1 3 INA Indonesia Indonesia 2 0 0 2 ISR Israel Israel 1 5 1 7 POL Poland Poland 1 4 5 10 KAZ Kazakhstan Kazakhstan 1 3 3 7 JAM Jamaica Jamaica 1 3 2 6 RSA South Africa South Africa 1 3 2 6 THA Thailand Thailand 1 3 2 6 AIN AIN AIN 1 3 1 5 ETH Ethiopia Ethiopia 1 3 0 4 SUI Switzerland Switzerland 1 2 5 8 ECU Ecuador Ecuador 1 2 2 5 POR Portugal Portugal 1 2 1 4 GRE Greece Greece 1 1 6 8 ARG Argentina Argentina 1 1 1 3 EGY Egypt Egypt 1 1 1 3 TUN Tunisia Tunisia 1 1 1 3 BOT Botswana Botswana 1 1 0 2 CHI Chile Chile 1 1 0 2 LCA Saint Lucia Saint Lucia 1 1 0 2 UGA Uganda Uganda 1 1 0 2 DOM Dominican Republic Dominican Republic 1 0 2 3 GUA Guatemala Guatemala 1 0 1 2 MAR Morocco Morocco 1 0 1 2 DMA Dominica Dominica 1 0 0 1 PAK Pakistan Pakistan 1 0 0 1 TUR Türkiye Türkiye 0 3 5 8 MEX Mexico Mexico 0 3 2 5 ARM Armenia Armenia 0 3 1 4 COL Colombia Colombia 0 3 1 4 PRK DPR Korea Democratic People's Republic of Korea 0 2 4 6 KGZ Kyrgyzstan Kyrgyzstan 0 2 4 6 LTU Lithuania Lithuania 0 2 2 4 IND India India 0 1 5 6 MDA Republic of Moldova Republic of Moldova 0 1 3 4 KOS Kosovo Kosovo 0 1 1 2 CYP Cyprus Cyprus 0 1 0 1 FIJ Fiji Fiji 0 1 0 1 JOR Jordan Jordan 0 1 0 1 MGL Mongolia Mongolia 0 1 0 1 PAN Panama Panama 0 1 0 1 TJK Tajikistan Tajikistan 0 0 3 3 ALB Albania Albania 0 0 2 2 GRN Grenada Grenada 0 0 2 2 MAS Malaysia Malaysia 0 0 2 2 PUR Puerto Rico Puerto Rico 0 0 2 2 CPV Cabo Verde Cabo Verde 0 0 1 1 CIV Côte d'Ivoire Côte d'Ivoire 0 0 1 1 EOR EOR Refugee Olympic Team 0 0 1 1 PER Peru Peru 0 0 1 1 QAT Qatar Qatar 0 0 1 1 SGP Singapore Singapore 0 0 1 1 SVK Slovakia Slovakia 0 0 1 1 ZAM Zambia Zambia 0 0 1 1

In [0]:
display(medallist_df)

medal_date medal_type medal_code name gender country_long nationality_long discipline event birth_date code_athlete is_medallist 2024-07-27 Gold Medal 1.0 EVENEPOEL Remco Male Belgium Belgium Cycling Road Men's Individual Time Trial 2000-01-25 1903136 true 2024-07-27 Silver Medal 2.0 GANNA Filippo Male Italy Italy Cycling Road Men's Individual Time Trial 1996-07-25 1923520 true 2024-07-27 Bronze Medal 3.0 van AERT Wout Male Belgium Belgium Cycling Road Men's Individual Time Trial 1994-09-15 1903147 true 2024-07-27 Gold Medal 1.0 BROWN Grace Female Australia Australia Cycling Road Women's Individual Time Trial 1992-07-07 1940173 true 2024-07-27 Silver Medal 2.0 HENDERSON Anna Female Great Britain Great Britain Cycling Road Women's Individual Time Trial 1998-11-14 1912525 true 2024-07-27 Bronze Medal 3.0 DYGERT Chloe Female United States of America United States of America Cycling Road Women's Individual Time Trial 1997-01-01 1955079 true 2024-07-27 Gold Medal 1.0 OH Sanguk Male Republic of Korea Republic of Korea Fencing Men's Sabre Individual 1996-09-30 1927149 true 2024-07-27 Silver Medal 2.0 FERJANI Fares Male Tunisia Tunisia Fencing Men's Sabre Individual 1997-07-22 1937783 true 2024-07-27 Bronze Medal 3.0 SAMELE Luigi Male Italy Italy Fencing Men's Sabre Individual 1987-07-25 1924595 true 2024-07-27 Gold Medal 1.0 KONG Man Wai Vivian Female Hong Kong, China Hong Kong, China Fencing Women's Épée Individual 1994-02-08 1963262 true 2024-07-27 Silver Medal 2.0 MALLO-BRETON Auriane Female France France Fencing Women's Épée Individual 1993-10-11 1916183 true 2024-07-27 Bronze Medal 3.0 MUHARI Eszter Female Hungary Hungary Fencing Women's Épée Individual 2002-09-30 1946375 true 2024-07-27 Gold Medal 1.0 SMETOV Yeldos Male Kazakhstan Kazakhstan Judo Men -60 kg 1992-09-09 1935408 true 2024-07-27 Silver Medal 2.0 MKHEIDZE Luka Male France France Judo Men -60 kg 1996-01-05 1891304 true 2024-07-27 Bronze Medal 3.0 NAGAYAMA Ryuju Male Japan Japan Judo Men -60 kg 1996-04-15 1896752 true 2024-07-27 Bronze Medal 3.0 GARRIGOS Francisco Male Spain Spain Judo Men -60 kg 1994-12-09 1563544 true 2024-07-27 Gold Medal 1.0 TSUNODA Natsumi Female Japan Japan Judo Women -48 kg 1992-08-06 1896735 true 2024-07-27 Silver Medal 2.0 BAVUUDORJ Baasankhuu Female Mongolia Mongolia Judo Women -48 kg 1999-11-26 1914467 true 2024-07-27 Bronze Medal 3.0 BOUKLI Shirine Female France France Judo Women -48 kg 1999-01-24 1891280 true 2024-07-27 Bronze Medal 3.0 BABULFATH Tara Female Sweden Sweden Judo Women -48 kg 2006-01-03 1571911 true 2024-07-27 Gold Medal 1.0 MAERTENS Lukas Male Germany Germany Swimming Men's 400m Freestyle 2001-12-27 1907192 true 2024-07-27 Silver Medal 2.0 WINNINGTON Elijah Male Australia Australia Swimming Men's 400m Freestyle 2000-05-05 1946172 true 2024-07-27 Bronze Medal 3.0 KIM Woomin Male Republic of Korea Republic of Korea Swimming Men's 400m Freestyle 2001-08-24 4654306 true 2024-07-27 Gold Medal 1.0 TITMUS Ariarne Female Australia Australia Swimming Women's 400m Freestyle 2000-09-07 1946150 true 2024-07-27 Silver Medal 2.0 McINTOSH Summer Female Canada Canada Swimming Women's 400m Freestyle 2006-08-18 1967140 true 2024-07-27 Bronze Medal 3.0 LEDECKY Katie Female United States of America United States of America Swimming Women's 400m Freestyle 1997-03-17 1935938 true 2024-07-28 Gold Medal 1.0 FOX Jessica Female Australia Australia Canoe Slalom Women's Kayak Single 1994-06-11 1940205 true 2024-07-28 Silver Medal 2.0 ZWOLINSKA Klaudia Female Poland Poland Canoe Slalom Women's Kayak Single 1998-12-18 1942126 true 2024-07-28 Bronze Medal 3.0 WOODS Kimberley Female Great Britain Great Britain Canoe Slalom Women's Kayak Single 1995-09-08 1896045 true 2024-07-28 Gold Medal 1.0 FERRAND PREVOT Pauline Female France France Cycling Mountain Bike Women's Cross-country 1992-02-10 1895672 true 2024-07-28 Silver Medal 2.0 BATTEN Haley Female United States of America United States of America Cycling Mountain Bike Women's Cross-country 1998-09-19 19

In [0]:
display(athlete_df)

code name gender country disciplines birth_date 1550150 PAUL Georges Julien Male Mauritius Badminton 1996-01-07 1554968 MEKTIC Nikola Male Croatia Tennis 1988-12-24 1561253 QUINTINO Jessica Female Brazil Handball 1991-04-17 1563335 QUAKE Male Chinese Taipei Breaking 1999-09-21 1564559 TAKAYAWA Gerard Male Fiji Judo 2005-11-07 1566441 FRANK Tanja Female Austria Sailing 1993-01-24 1572558 AASTEDT Sofia Female Sweden Swimming null 1572617 BAUER Christina Female France Volleyball 1988-01-01 1573136 LIZAKOWSKA Weronika Female Poland Athletics 1998-11-02 1879111 OUMIHA Sofiane Male France Boxing 1994-12-23 1879831 FOPPA Pauletta Female France Handball 2000-12-22 1887978 CIOBANU Victor Male Republic of Moldova Wrestling 1992-10-07 1888156 KITAGAWA Hikaru Female Japan Football 1997-05-10 1888973 TOLBA Youssof Male Egypt Archery null 1891002 DAVIDSON Madaline Female New Zealand Trampoline Gymnastics 1999-01-08 1899035 SANFORD Liam Male Great Britain Hockey 1996-03-14 1899257 STOCKSCHLAEDER Johanna Maria Female Germany Handball 1995-02-11 1901562 de la CRUZ de PENA Bethania Female Dominican Republic Volleyball 1987-05-13 1901750 WU Tongtong Female China Basketball 1994-06-27 1901756 SUN Mengran Female China Basketball 1992-07-16 1902180 HASEGAWA Akiko Female Japan Beach Volleyball 1985-11-30 1906480 FINGER Anton Male Germany Rowing 1998-08-01 1907194 SORGIUS Timo Male Germany Swimming null 1907658 DANANI Santiago Male Argentina Volleyball 1995-12-12 1911929 SAIDY Fabrisio Male France Athletics null 1913218 LIN Xiyu Janet Female China Golf 1996-02-25 1917762 SKINNER Avery Female United States Volleyball 1999-04-25 1920302 KRAFZIK Carolina Female Germany Athletics 1995-03-27 1924385 ATKIN Sam Male Great Britain Athletics 1993-03-14 1925355 CHAMIZO MARQUEZ Frank Male Italy Wrestling 1992-07-10 1925641 BERTOCCHI Elena Female Italy Diving null 1925806 BANCHELLI Caterina Female Italy Water Polo 2000-09-25 1539131 BERTEMES Bob Male Luxembourg Athletics 1993-05-24 1539954 WALSH Grainne Female Ireland Boxing 1995-10-13 1551330 NALBANTOVA Kaloyana Female Bulgaria Badminton 2006-03-06 1552154 ACCAME Ilaria Elvira Female Italy Athletics 2001-08-31 1554997 LOEFQVIST Olivia Female Sweden Handball 1998-07-13 1561242 ARENHART Barbara Female Brazil Handball 1986-10-04 1562779 ANDERSON Navasky Male Jamaica Athletics 2000-01-21 1562874 MUELLER Svenja Female Germany Beach Volleyball 2001-02-13 1568167 ONDER Ahmet Male Türkiye Artistic Gymnastics null 1574118 SOYIZWAPI Siviwe Male South Africa Rugby Sevens 1992-12-07 1878450 REINKIND Harald Male Norway Handball 1992-08-17 1878525 BRUN Kristoffer Male Norway Rowing 1988-04-07 1879856 ZAADI DEUNA Grace Female France Handball 1993-07-07 1888831 SEJA Arturas Male Lithuania Canoe Sprint 1996-03-17 1889162 FAROUK Mohamed Male Egypt Diving 2002-12-13 1891289 AGBEGNENOU Clarisse Female France Judo 1992-10-25 1892105 HABARTA Tomas Male Czechia Athletics 2003-07-10 1892647 KWIZERA Rodrigue Male Burundi Athletics null 1895553 BACARI Elie Male Belgium Athletics 2003-10-14 1896822 ALIKULOV Khusniddin Male Uzbekistan Football 1999-04-04 1898472 EMOMALI Nurali Male Tajikistan Judo 2002-04-08 1899731 BECKETT Michael Male Great Britain Sailing 1995-03-27 1901063 FIELDMAN Henry Male Great Britain Rowing 1988-11-25 1901337 NOSKOVA Linda Female Czechia Tennis null 1901954 WATANABE Yuta Male Japan Basketball 1994-10-13 1903122 GOMMERS Aiko Female Belgium Cycling BMX Racing 2004-03-18 1908825 VO Thi Kim Anh Female Vietnam Boxing 1997-07-29 1910646 BONNIN Marie-Julie Female France Athletics 2001-12-17 1912009 RICHARDSON Lewis Male Great Britain Boxing 1997-06-04 1913958 ZHAO Nan Female China Shooting 2004-05-14 1914295 ODKHUU Tsetsentsengel Male Mongolia Judo 1999-10-18 1917792 LIJTENSTEIN Guillermo Male Uruguay Rugby Sevens 1990-09-14 1918706 ISHIKAWA Yuki Male Japan Volleyball 1995-12-11 1921364 RUSSO Roberto Male Italy Volleyball 1997-02-23 1924384 ASHER-SMITH Dina Female Great Britain Athletics null 1924401 CAIRESS Emile Male